In [1]:
# Directories
import os
os.chdir(r"E:\academy\OneDrive - IIT Delhi\3. IIT DELHI\2. Academics\1_PAPER\2_Analysis")
print(os.getcwd())

E:\academy\OneDrive - IIT Delhi\3. IIT DELHI\2. Academics\1_PAPER\2_Analysis


In [2]:
#Array packages
import pandas as pd
import numpy as np
import xarray as xr
import netCDF4 as nc4

from scipy.stats import kendalltau
import pymannkendall as mk

#plots
import matplotlib.pyplot as plt
import rioxarray as rio
import geopandas as gpd
from shapely.geometry import mapping

#Progress meter
from dask.diagnostics import ProgressBar
from tqdm import tqdm

# Directories
import os
import glob
import dask
#import h5netcdf
import scipy


C:\Users\sstar\anaconda3\envs\imed\Lib\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


# Teleconnection

In [16]:
import scienceplots
mdl=5
model=["LIS_MERRA2","LIS_IMD","LIS_CHIRPS","LIS_ERA5","LIS_IMDc","LIS_IMDcnew"]
var=['TotalPrecip_tavg','Evap_tavg','Qs_tavg','RE','RE_cleaned']


ds_RM = xr.open_mfdataset(f'DATA_p/LIS/{model[mdl]}/{model[mdl]}_reg_all.nc',engine='netcdf4', parallel=True,chunks={'time': 'auto'})
basin=ds_RM.region.values
phases = ['El Nino','La Nina','test','ratio']
df = pd.DataFrame(columns=phases,index=basin)
df= df.apply(pd.to_numeric, errors='coerce')

# Loading climatic oscillation
CO=pd.read_csv('DATA_r/3_Climate_oscillation/CO_new.csv')
CO['DATE'] = pd.to_datetime(CO.DATE,format='%d-%m-%Y')
CO.set_index('DATE', inplace=True)
enso = CO.loc[ds_RM.time][['ENSO','ENSO_phase']]
xr_enso=xr.DataArray(np.array(enso["ENSO"]),coords=[ds_RM.time.values],dims=["time"])
##el nino la nina
elnino=enso[enso["ENSO_phase"]=="EL NINO"].index
lanina=enso[enso["ENSO_phase"]=="LA NINA"].index

In [28]:
var=['RE_cleaned','TotalPrecip_tavg','Qs_tavg']
var_l=['Runoff efficiency','Rainfall','Runoff']
ssn=['All','Monsoon','Winter']
var_ssn = [[a, b] for a in var_l for b in ssn]
ssn_m=[range(1,13),[6,7,8,9],[11,12,1,2,3]]
anot=['a','b','c']

In [29]:
from scipy.stats import ttest_ind
from scipy.stats import mannwhitneyu

import scienceplots
plt.style.use(['science','no-latex','bright'])
result=[]
for ss in range(1,2):
    
    fig, ax = plt.subplots(figsize=(20, 17),nrows=3,gridspec_kw={'hspace': 0.05},dpi=600)  # Increased size
 
    for vr in range(3):
        
        ds=ds_RM [var[vr]]  
    
        elnino1=elnino[elnino.month.isin(ssn_m[ss])]
        lanina1=lanina[lanina.month.isin(ssn_m[ss])]
    
        
        for i, Reg in enumerate(basin):
        
            ppt_el=ds.sel(region=Reg,time=elnino1).compute().values
            ppt_la=ds.sel(region=Reg,time=lanina1).compute().values
            
            _, p_value = mannwhitneyu(ppt_el, ppt_la)
            #_, p_value = ttest_ind(ppt_el, ppt_la)
            
            df.iloc[i,0]=ds.sel(region=Reg,time=elnino1).mean(dim='time').compute().values
            df.iloc[i,1]=ds.sel(region=Reg,time=lanina1).mean(dim='time').compute().values
            df.iloc[i,2]= p_value 
            
            
            if ppt_el.mean()  > ppt_la.mean():
                ratio = ppt_el.mean() / ppt_la.mean() 
            else:
                ratio = ppt_la.mean() / ppt_el.mean()
                
            df.iloc[i,3]= ratio

        
        colors = ['red','dodgerblue'] 
        
        
        #ax[1].invert_yaxis() 
        df[['El Nino','La Nina']].plot.bar(rot=45, ax=ax[vr],color= colors,width=0.6,edgecolor='white')
        [x.set_linewidth(1.7) for x in ax[vr].spines.values()]
        ax[vr].grid(True, color= 'grey', alpha=0.1, linestyle='dotted')
        ax[vr].set_ylim(0,ds_RM[var[vr]].sel(time=ds_RM['time.month'].isin([ssn_m[ss]])).quantile(0.99).compute())
        
        ax[vr].text(0.025, 0.92,f'{anot[vr]})',fontsize=29,color='black',weight='bold',transform=ax[vr].transAxes,ha='center', va='center')
        ax[vr].set_ylabel(var_l[vr],fontsize=30.5,labelpad=17)


        for i in range(len(df)):
            if df.iloc[i, 2] < 0.05:  # Check p-value
                ax[vr].text(i, df.iloc[i, :2].max() + 0.01 * df.iloc[:, :2].max().max(), '*', fontsize=19, color='black', ha='center')
                ax[vr].text(i, df.iloc[i, :2].max() + 0.150 * df.iloc[:, :2].max().max(), f'{df.iloc[i, 3]:.2f}', fontsize=22, color='black', ha='center')
            
    ax[0].yaxis.set_tick_params(which='both', bottom=True, top=False,labelsize=26.5) 
    ax[0].xaxis.set_tick_params(which='both', left=True, right=False,labelbottom=False,labelsize=28)
    ax[1].yaxis.set_tick_params(which='both', left=True, right=False,labelsize=26.5)
    ax[1].xaxis.set_tick_params(which='both', left=True, right=False,labelbottom=False,labelsize=25.5)
    ax[2].yaxis.set_tick_params(which='both', left=True, right=False,labelsize=26.5)
    ax[2].xaxis.set_tick_params(which='both', left=True, right=False,labelsize=28)
    
    
    ax[0].legend(loc='upper right', bbox_to_anchor=(0.90, 1),title_fontsize=30,ncol=4,fontsize=24)
    ax[1].legend().remove()
    ax[2].legend().remove()

    plt.tight_layout()
    plt.savefig(f'4_Teleconnection/outputs/ENSO_REG_{ssn[ss]}.jpeg', bbox_inches='tight')
    plt.show()

C:\Users\sstar\AppData\Local\Temp\ipykernel_20552\2356872799.py:70: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  plt.tight_layout()


### % change from normal

In [20]:
#var=['TotalPrecip_tavg','RE_cleaned','Qs_tavg']
var=['TotalPrecip_tavg','Qs_tavg']



ssn=['All','Monsoon','Winter']
ssn_m=[range(1,13),[5,6,7,8,9],[11,12,1,2,3]]

cols = ['Rainfall_el','Rainfall_la','RE_el','RE_la']
df = pd.DataFrame(columns=cols,index=basin)
df= df.apply(pd.to_numeric, errors='coerce')
df

Rainfall_el  Rainfall_la  RE_el  RE_la
Indus                 NaN          NaN    NaN    NaN
Ganga                 NaN          NaN    NaN    NaN
WFKS                  NaN          NaN    NaN    NaN
Sabarmati             NaN          NaN    NaN    NaN
Mahi                  NaN          NaN    NaN    NaN
Tapi                  NaN          NaN    NaN    NaN
Narmada               NaN          NaN    NaN    NaN
Brahmaputra           NaN          NaN    NaN    NaN
Subarnarekha          NaN          NaN    NaN    NaN
Brahmani              NaN          NaN    NaN    NaN
Mahanadi              NaN          NaN    NaN    NaN
Godavari              NaN          NaN    NaN    NaN
Krishna               NaN          NaN    NaN    NaN
Penanr                NaN          NaN    NaN    NaN
Cauvery               NaN          NaN    NaN    NaN
EFPK                  NaN          NaN    NaN    NaN
EFMP                  NaN          NaN    NaN    NaN
West Flowing          NaN          NaN    NaN    NaN

In [22]:
from scipy.stats import ttest_ind
from scipy.stats import mannwhitneyu

import scienceplots
plt.style.use(['science','no-latex','bright'])
result=[]
inc=[0,2]
for ss in range(1,2):
    
    for vr in range(2):
        
        ds=ds_RM [var[vr]]  
    
        elnino1=elnino[elnino.month.isin(ssn_m[ss])]
        lanina1=lanina[lanina.month.isin(ssn_m[ss])]
    
        
        for i, Reg in enumerate(basin):

            full=ds.sel(region=Reg,time=ds['time.month'].isin(ssn_m[ss])).mean(dim='time').compute().values
            ppt_el=ds.sel(region=Reg,time=elnino1).mean(dim='time').compute().values
            ppt_la=ds.sel(region=Reg,time=lanina1).mean(dim='time').compute().values
            
            _, p_value = mannwhitneyu(ppt_el, ppt_la)
            #_, p_value = ttest_ind(ppt_el, ppt_la)
            
            df.iloc[i,inc[vr]]=(ppt_el-full)/full
            df.iloc[i,inc[vr]+1]=(ppt_la-full)/full
  

df=df*100       
 

In [24]:
df

Rainfall_el  Rainfall_la      RE_el      RE_la
Indus          -13.048571     2.282122   2.525849 -13.564641
Ganga          -16.093051     8.409836 -19.856555  14.465262
WFKS           -19.787641     5.668286 -25.656871  15.744834
Sabarmati      -18.298110     1.148109 -21.012088  -6.740856
Mahi           -16.175286    -3.587261 -24.395311 -19.989371
Tapi           -14.248141     4.160154 -25.423707   3.159485
Narmada        -17.718121     3.926316 -28.199034   2.631109
Brahmaputra      2.383656     1.111469  15.474497  -2.477954
Subarnarekha    -9.668279     8.121510 -15.827033  18.332846
Brahmani       -12.822824    10.409776 -23.578641  18.999097
Mahanadi       -14.805971     2.632266 -23.748099  -3.627797
Godavari       -17.335481     8.044363 -39.523605  10.440098
Krishna        -12.570792    11.594389 -28.468392  13.679704
Penanr         -17.551359    19.690327 -39.444968  39.006054
Cauvery        -10.329935    13.487417 -29.089448  30.869429
EFPK           -16.008811    14.801407 -25.892893  16.858864
EFMP           -12.482633     6.685471 -25.529429   1.627194
West Flowing   -10.264301     2.495411 -15.406531   2.601595

# 2 WITH SPI

In [ ]:
import scienceplots
mdl=5
model=["LIS_MERRA2","LIS_IMD","LIS_CHIRPS","LIS_ERA5","LIS_IMDc","LIS_IMDcnew"]
var=['TotalPrecip_tavg','Evap_tavg','Qs_tavg','RE','RE_cleaned']


ds_RM = xr.open_mfdataset(f'DATA_p/LIS/{model[mdl]}/{model[mdl]}_reg_SPI1.nc',engine='netcdf4', parallel=True,chunks={'time': 'auto'})
basin=ds_RM.region.values
phases = ['La Nina-El Nino','test']
df = pd.DataFrame(columns=phases,index=basin)
df= df.apply(pd.to_numeric, errors='coerce')

# Loading climatic oscillation
CO=pd.read_csv('DATA_r/3_Climate_oscillation/CO_new.csv')
CO['DATE'] = pd.to_datetime(CO.DATE,format='%d-%m-%Y')
CO.set_index('DATE', inplace=True)
enso = CO.loc[ds_RM.time][['ENSO','ENSO_phase']]
xr_enso=xr.DataArray(np.array(enso["ENSO"]),coords=[ds_RM.time.values],dims=["time"])
##el nino la nina
elnino=enso[enso["ENSO_phase"]=="EL NINO"].index
lanina=enso[enso["ENSO_phase"]=="LA NINA"].index

var=['RE_cleaned','TotalPrecip_tavg','Qs_tavg']
var_l=['Runoff Efficiency','Rainfall','Runoff']
ssn=['All','Monsoon','Winter']
var_ssn = [[a, b] for a in var_l for b in ssn]
ssn_m=[range(1,13),[5,6,7,8,9],[11,12,1,2,3]]
anot=['a','b','c']

In [27]:
from scipy.stats import ttest_ind
import scienceplots
plt.style.use(['science','no-latex','bright'])
result=[]
for ss in range(2,3):
    
    fig, ax = plt.subplots(figsize=(20, 17),nrows=3,gridspec_kw={'hspace': 0.05},dpi=600)  # Increased size
 
    for vr in range(3):
        
        ds=ds_RM [var[vr]]  
    
        elnino1=elnino[elnino.month.isin(ssn_m[ss])]
        lanina1=lanina[lanina.month.isin(ssn_m[ss])]
    
        
        for i, Reg in enumerate(basin):
        
            ppt_el=ds.sel(region=Reg,time=elnino1).compute().values
            ppt_la=ds.sel(region=Reg,time=lanina1).compute().values
            
            _, p_value = ttest_ind(ppt_el, ppt_la, axis=0)
            
            df.iloc[i,0]=ppt_la.mean()-ppt_el.mean()
            df.iloc[i,1]=p_value 
          


        
        colors = ['red','dodgerblue'] 
        
        
        #ax[1].invert_yaxis() 
        df[['La Nina-El Nino']].plot.bar(rot=45, ax=ax[vr],color= colors,width=0.6,edgecolor='white')
        [x.set_linewidth(1.7) for x in ax[vr].spines.values()]
        ax[vr].grid(True, color= 'grey', alpha=0.1, linestyle='dotted')
        ax[vr].set_ylim(-1,1)
        
        ax[vr].text(0.025, 0.92,f'{anot[vr]})',fontsize=29,color='black',weight='bold',transform=ax[vr].transAxes,ha='center', va='center')
        ax[vr].set_ylabel(var_l[vr],fontsize=30.5,labelpad=17)


        for i in range(len(df)):
            if df.iloc[i, 1] < 0.05:  # Check p-value
                ax[vr].text(i, df.iloc[i, :2].max() + 0.05 * df.iloc[:, :2].max().max(), '*', fontsize=25, color='black', ha='center')
            
            
    ax[0].yaxis.set_tick_params(which='both', bottom=True, top=False,labelsize=26.5) 
    ax[0].xaxis.set_tick_params(which='both', left=True, right=False,labelbottom=False,labelsize=28)
    ax[1].yaxis.set_tick_params(which='both', left=True, right=False,labelsize=26.5)
    ax[1].xaxis.set_tick_params(which='both', left=True, right=False,labelbottom=False,labelsize=25.5)
    ax[2].yaxis.set_tick_params(which='both', left=True, right=False,labelsize=26.5)
    ax[2].xaxis.set_tick_params(which='both', left=True, right=False,labelsize=28)
    
    
    ax[0].legend(loc='upper right', bbox_to_anchor=(0.90, 1),title_fontsize=30,ncol=4,fontsize=24)
    ax[1].legend().remove()
    ax[2].legend().remove()

    plt.tight_layout()
    #plt.savefig(f'4_Teleconnection/outputs/ENSO_REG_{ssn[ss]}.jpeg', bbox_inches='tight')
    plt.show()

C:\Users\sstar\AppData\Local\Temp\ipykernel_324\1734121865.py:60: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  plt.tight_layout()


# FUNCTIONS

In [66]:
def get_sub(x): 
    normal = "ABCDEFGHIJKLMNOPQRSTUVWXYZabcdefghijklmnopqrstuvwxyz0123456789+-=()"
    sub_s = "ₐ₈cdₑբGₕᵢⱼₖₗₘₙₒₚQᵣₛₜᵤᵥwₓᵧZₐ♭꜀ᑯₑբ₉ₕᵢⱼₖₗₘₙₒₚ૧ᵣₛₜᵤᵥwₓᵧ₂₀₁₂₃₄₅₆₇₈₉₊₋₌₍₎"
    res = x.maketrans(''.join(normal), ''.join(sub_s)) 
    return x.translate(res) 
  
# display subscript 
print('H{}SO{}'.format(get_sub('2'),get_sub('4'))) #H₂SO₄ 

H₂SO₄
